In [4]:
import xesmf as xe
import xarray as xr
import pandas as pd
from pathlib import Path
import warnings

In [5]:
odir = '../CMIP6/2deg/'

In [4]:
with xr.open_dataset('../ERA5_UltraLowRes/ERA5_UltraLowRes_Invariant.nc') as dse:
    dse = dse.load()

In [5]:
dse

<xarray.Dataset> Size: 132kB
Dimensions:    (latitude: 90, longitude: 180)
Coordinates:
  * latitude   (latitude) float64 720B 89.0 87.0 85.0 83.0 ... -85.0 -87.0 -89.0
  * longitude  (longitude) float64 1kB -179.0 -177.0 -175.0 ... 177.0 179.0
Data variables:
    lsm        (latitude, longitude) float32 65kB 0.0 0.0 0.0 ... 1.0 1.0 1.0
    orography  (latitude, longitude) float32 65kB 0.1735 0.1914 ... 3.017e+03
Attributes:
    Conventions:  CF-1.7
    institution:  European Centre for Medium-Range Weather Forecasts

## CMIP6 and CMIP5 on ERA 

In [6]:
SSPs = ['ssp126', 'ssp245', 'ssp370', 'ssp585']
GCMs = ['BCC-CSM2-MR', 'CAMS-CSM1-0', 'CESM2', 'CESM2-WACCM', 
        'EC-Earth3', 'EC-Earth3-Veg', 'FGOALS-f3-L', 'GFDL-ESM4', 
        'INM-CM4-8', 'INM-CM5-0', 'MPI-ESM1-2-HR', 'MRI-ESM2-0', 
        'NorESM2-MM']

In [7]:
out = xr.Dataset()
out_pr = xr.Dataset()

out_mon = xr.Dataset()
out_mon_pr = xr.Dataset()

In [7]:
# CMIP6
df_gcm = pd.read_csv('/home/users/fmaussion/www_oggm/cmip6/all_gcm_list.csv', index_col=0)
df_gcm = df_gcm.loc[df_gcm.rea == 'r1i1p1f1']

In [9]:
res = '2deg'

In [10]:
time_coder = xr.coders.CFDatetimeCoder(use_cftime=True)

In [11]:
for gcm in GCMs:
    for ssp in SSPs:
        
        print(f'{gcm}_{ssp}')
            
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'tas')]
        assert len(s) == 1

        with xr.open_dataset(s.path.iloc[0], decode_times=time_coder) as ds:
            
            # Save attrs
            ds_attrs = ds.attrs.copy()
            var_attrs = {v: ds[v].attrs.copy() for v in ds.data_vars}
            var_encoding = {v: ds[v].encoding.copy() for v in ds.data_vars}
            
            ds = ds.sel(time=slice('1979', '2099'))
            
            # convert the cftime dates
            cftime_dates = ds.time.values
            converted_dates = pd.to_datetime([f"{date.year}-{date.month:02d}-01" for date in cftime_dates])
            ds["time"] = converted_dates
            
            if ssp == SSPs[0]:
                # do regridder
                print('Init regridder ...')
                regridder = xe.Regridder(ds, dse, method='conservative', periodic=True)
            dsout = regridder(ds)
            
            # Restore attrs
            dsout.attrs.update(ds_attrs)
            for v in dsout.data_vars:
                if v in var_attrs:
                    dsout[v].attrs.update(var_attrs[v])
                    dsout[v].encoding.update(var_encoding[v])
            
            folder = f"../CMIP6/{res}/{s.folder.values[0]}"
            if '_r1i1p1f1_' not in s.fname.values[0]:
                raise RuntimeError('no')
            filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
            Path(folder).mkdir(parents=True, exist_ok=True)
            dsout.to_netcdf(folder + '/' + filename)

        # Now precip
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'pr')]
        assert len(s) == 1
        
        with xr.open_dataset(s.path.iloc[0], decode_times=time_coder) as ds:
            
            # Save attrs
            ds_attrs = ds.attrs.copy()
            var_attrs = {v: ds[v].attrs.copy() for v in ds.data_vars}
            var_encoding = {v: ds[v].encoding.copy() for v in ds.data_vars}
            
            ds = ds.sel(time=slice('1979', '2099'))
            
            # convert the cftime dates
            cftime_dates = ds.time.values
            converted_dates = pd.to_datetime([f"{date.year}-{date.month:02d}-01" for date in cftime_dates])
            ds["time"] = converted_dates
        
            dsout = regridder(ds)
            
            # Restore attrs
            dsout.attrs.update(ds_attrs)
            for v in dsout.data_vars:
                if v in var_attrs:
                    dsout[v].attrs.update(var_attrs[v])
                    dsout[v].encoding.update(var_encoding[v])
            
            folder = f"../CMIP6/{res}/{s.folder.values[0]}"
            
            if '_r1i1p1f1_' not in s.fname.values[0]:
                raise RuntimeError('no')
            filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
            Path(folder).mkdir(parents=True, exist_ok=True)
            dsout.to_netcdf(folder + '/' + filename)
            
print('done')

BCC-CSM2-MR_ssp126
Init regridder ...
BCC-CSM2-MR_ssp245
BCC-CSM2-MR_ssp370
BCC-CSM2-MR_ssp585
CAMS-CSM1-0_ssp126
Init regridder ...
CAMS-CSM1-0_ssp245
CAMS-CSM1-0_ssp370
CAMS-CSM1-0_ssp585
CESM2_ssp126
Init regridder ...
CESM2_ssp245
CESM2_ssp370
CESM2_ssp585
CESM2-WACCM_ssp126
Init regridder ...
CESM2-WACCM_ssp245
CESM2-WACCM_ssp370
CESM2-WACCM_ssp585
EC-Earth3_ssp126
Init regridder ...
EC-Earth3_ssp245
EC-Earth3_ssp370
EC-Earth3_ssp585
EC-Earth3-Veg_ssp126
Init regridder ...
EC-Earth3-Veg_ssp245
EC-Earth3-Veg_ssp370
EC-Earth3-Veg_ssp585
FGOALS-f3-L_ssp126
Init regridder ...
FGOALS-f3-L_ssp245
FGOALS-f3-L_ssp370
FGOALS-f3-L_ssp585
GFDL-ESM4_ssp126
Init regridder ...
GFDL-ESM4_ssp245
GFDL-ESM4_ssp370
GFDL-ESM4_ssp585
INM-CM4-8_ssp126
Init regridder ...
INM-CM4-8_ssp245
INM-CM4-8_ssp370
INM-CM4-8_ssp585
INM-CM5-0_ssp126
Init regridder ...
INM-CM5-0_ssp245
INM-CM5-0_ssp370
INM-CM5-0_ssp585
MPI-ESM1-2-HR_ssp126
Init regridder ...
MPI-ESM1-2-HR_ssp245
MPI-ESM1-2-HR_ssp370
MPI-ESM1-2-HR_ss

In [12]:
print('done')

done


In [9]:
burl = 'https://cluster.klima.uni-bremen.de/~fmaussion/teaching/qcr/'

res = '2deg'

precip_list = ''
temp_list = ''
pet_list = ''
spei_list = ''

text = '````{dropdown} Monthly temperature at 2° resolution\n'

for gcm in GCMs:
    for ssp in SSPs:
            
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'tas')]
        assert len(s) == 1
        
        folder = f"CMIP6/{res}/{s.folder.values[0]}"
        filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
        filepath = burl + folder + '/' + filename
        
        if ssp == SSPs[0]:
            text += "```{dropdown} " + f"{s.folder.values[0]}\n"
            
        text += f"- [{gcm}_{ssp}]({filepath})\n"
        temp_list += f"{filepath}\n"
        
        if ssp == SSPs[-1]:
            text += "```\n"
            text += "\n"

text += "````\n"
text += "\n"

text += '````{dropdown} Monthly precipitation at 2° resolution\n'

for gcm in GCMs:
    for ssp in SSPs:
            
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'pr')]
        assert len(s) == 1
        
        folder = f"CMIP6/{res}/{s.folder.values[0]}"
        filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
        filepath = burl + folder + '/' + filename
        
        if ssp == SSPs[0]:
            text += "```{dropdown} " + f"{s.folder.values[0]}\n"
           
        text += f"- [{gcm}_{ssp}]({filepath})\n"
        precip_list += f"{filepath}\n"
        
        if ssp == SSPs[-1]:
            text += "```\n"
            text += "\n"

text += "````\n"
text += "\n"

text += '````{dropdown} Monthly PET at 2° resolution\n'

for gcm in GCMs:
    for ssp in SSPs:
            
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'pr')]
        assert len(s) == 1
        
        folder = f"CMIP6/{res}/{s.folder.values[0]}"
        filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
        filename = filename.replace('_pr.nc', '_pet.nc')
        filepath = burl + folder + '/' + filename
        
        if ssp == SSPs[0]:
            text += "```{dropdown} " + f"{s.folder.values[0]}\n"
           
        text += f"- [{gcm}_{ssp}]({filepath})\n"
        pet_list += f"{filepath}\n"
        
        if ssp == SSPs[-1]:
            text += "```\n"
            text += "\n"

text += "````\n"

text += '````{dropdown} Monthly SPEI at 2° resolution\n'

for gcm in GCMs:
    for ssp in SSPs:
            
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'pr')]
        assert len(s) == 1
        
        folder = f"CMIP6/{res}/{s.folder.values[0]}"
        filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
        filename = filename.replace('_pr.nc', '_spei.nc')
        filepath = burl + folder + '/' + filename
        
        if ssp == SSPs[0]:
            text += "```{dropdown} " + f"{s.folder.values[0]}\n"
           
        text += f"- [{gcm}_{ssp}]({filepath})\n"
        spei_list += f"{filepath}\n"
        
        if ssp == SSPs[-1]:
            text += "```\n"
            text += "\n"

text += "````\n"


with open(f"cmip6-list-{res}.md", "w") as f:
    f.write(text)

with open(f"cmip6-tas-list-{res}.txt", "w") as f:
    f.write(temp_list)

with open(f"cmip6-pr-list-{res}.txt", "w") as f:
    f.write(precip_list)

with open(f"cmip6-pet-list-{res}.txt", "w") as f:
    f.write(pet_list)

with open(f"cmip6-spei-list-{res}.txt", "w") as f:
    f.write(spei_list)

In [10]:
burl = 'https://cluster.klima.uni-bremen.de/~fmaussion/teaching/qcr/'

res = '075deg'

precip_list = ''
temp_list = ''
pet_list = ''
spei_list = ''

text = '````{dropdown} Monthly temperature at 0.75° resolution\n'

for gcm in GCMs:
    for ssp in SSPs:
            
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'tas')]
        assert len(s) == 1
        
        folder = f"CMIP6/{res}/{s.folder.values[0]}"
        filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
        filepath = burl + folder + '/' + filename
        
        if ssp == SSPs[0]:
            text += "```{dropdown} " + f"{s.folder.values[0]}\n"
            
        text += f"- [{gcm}_{ssp}]({filepath})\n"
        temp_list += f"{filepath}\n"
        
        if ssp == SSPs[-1]:
            text += "```\n"
            text += "\n"

text += "````\n"
text += "\n"

text += '````{dropdown} Monthly precipitation at 0.75° resolution\n'

for gcm in GCMs:
    for ssp in SSPs:
            
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'pr')]
        assert len(s) == 1
        
        folder = f"CMIP6/{res}/{s.folder.values[0]}"
        filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
        filepath = burl + folder + '/' + filename
        
        if ssp == SSPs[0]:
            text += "```{dropdown} " + f"{s.folder.values[0]}\n"
           
        text += f"- [{gcm}_{ssp}]({filepath})\n"
        precip_list += f"{filepath}\n"
        
        if ssp == SSPs[-1]:
            text += "```\n"
            text += "\n"

text += "````\n"
text += "\n"

text += '````{dropdown} Monthly PET at 0.75° resolution\n'

for gcm in GCMs:
    for ssp in SSPs:
            
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'pr')]
        assert len(s) == 1
        
        folder = f"CMIP6/{res}/{s.folder.values[0]}"
        filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
        filename = filename.replace('_pr.nc', '_pet.nc')
        filepath = burl + folder + '/' + filename
        
        if ssp == SSPs[0]:
            text += "```{dropdown} " + f"{s.folder.values[0]}\n"
           
        text += f"- [{gcm}_{ssp}]({filepath})\n"
        pet_list += f"{filepath}\n"
        
        if ssp == SSPs[-1]:
            text += "```\n"
            text += "\n"

text += "````\n"

text += '````{dropdown} Monthly SPEI at 0.75° resolution\n'

for gcm in GCMs:
    for ssp in SSPs:
            
        s = df_gcm.loc[(df_gcm.ssp == ssp) & (df_gcm.gcm == gcm) & (df_gcm['var'] == 'pr')]
        assert len(s) == 1
        
        folder = f"CMIP6/{res}/{s.folder.values[0]}"
        filename = s.fname.values[0].replace('_r1i1p1f1_', '_regridded_')
        filename = filename.replace('_pr.nc', '_spei.nc')
        filepath = burl + folder + '/' + filename
        
        if ssp == SSPs[0]:
            text += "```{dropdown} " + f"{s.folder.values[0]}\n"
           
        text += f"- [{gcm}_{ssp}]({filepath})\n"
        spei_list += f"{filepath}\n"
        
        if ssp == SSPs[-1]:
            text += "```\n"
            text += "\n"

text += "````\n"


with open(f"cmip6-list-{res}.md", "w") as f:
    f.write(text)

with open(f"cmip6-tas-list-{res}.txt", "w") as f:
    f.write(temp_list)

with open(f"cmip6-pr-list-{res}.txt", "w") as f:
    f.write(precip_list)

with open(f"cmip6-pet-list-{res}.txt", "w") as f:
    f.write(pet_list)

with open(f"cmip6-spei-list-{res}.txt", "w") as f:
    f.write(spei_list)